In [36]:
from googleads import adwords
import pandas as pd
from StringIO import StringIO
import collections

In [77]:
class adwords_accounts(object):
    def __init__(self, start, end, version='v201705'):
        self._page_size = 500
        self._client = adwords.AdWordsClient.LoadFromStorage()
        self._version = version
        self._all_accounts = {}
        self._new_accounts_df = None
        self._start = start
        self._end = end
        self._max_operations = 3000
            
    def pull_accounts(self):
        mcc = self._client.GetService('ManagedCustomerService', version=self._version)
        offset = 0
        selector = {
            'fields': ['CustomerId', 'Name'],
            'predicates': [{'field' : 'ExcludeHiddenAccounts',
                            'operator' : 'EQUALS' ,
                            'values' : 'true'
                            }],
            'paging': {
                'startIndex': str(offset),
                'numberResults': str(self._page_size)
            }
        }
        more_pages = True
        while more_pages:
            page = mcc.get(selector)
            if 'entries' in page and page['entries']:
                for account in page['entries']:
                    self._all_accounts[account['customerId']] = account['name']
            offset += self._page_size
            selector['paging']['startIndex'] = str(offset)
            more_pages = offset < int(page['totalNumEntries'])
    
    def get_accounts(self, filter_old=True):
        if not self._all_accounts:
            self.pull_accounts()
        df = pd.DataFrame(self._all_accounts.items())
        df.columns = ['account_id', 'account_name']
        if filter_old:
            df = df[df.account_name.str.contains('^[a-z]{2}\_jobseeker\_usd\_.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_aed\_.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_app\_promo.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_app\_active.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_disabled.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_display\_.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_content\_.*', regex=True, na=False)]
            df = df[~df.account_name.str.contains('^.*\_dsa\_.*', regex=True, na=False)]
            df['country'] = df.account_name.apply(lambda x: x[0:2])
        self._new_accounts_df = df.sort_values('country')
    
    def get_all_countries(self):
        if self._new_accounts_df is None:
            self.get_accounts()   
        return self._new_accounts_df.groupby('country')['country'].count().to_dict()
    
    def country_accounts(self, country):
        df = self._new_accounts_df[self._new_accounts_df.country==country]
        return df.set_index('account_id')['account_name'].to_dict()
    
    def get_paused_stardard_text_ads(self, account_id):
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        qry = ('SELECT CampaignId, CampaignStatus, AdGroupId, AdGroupStatus, Id, AdType, Impressions, Clicks, Cost FROM '
               'AD_PERFORMANCE_REPORT WHERE Status IN [PAUSED] AND CampaignStatus in [ENABLED, PAUSED] '
               'AND AdGroupStatus in [ENABLED, PAUSED] DURING {0}, {1}').format(self._start, self._end)  
        stream_data = report_downloader.DownloadReportAsStringWithAwql(qry, 'CSV',
                skip_report_header=True, skip_column_header=False,
                skip_report_summary=True, include_zero_impressions=True)
        report_data = StringIO(stream_data)
        report_df = pd.DataFrame.from_csv(report_data, sep=',').reset_index()
        report_df = report_df.sort_values('Impressions', ascending=True)
        return report_df[report_df['Ad type']=='Text ad']
    
      
    def delete_multiple_ads(self, account_id, df_data, verbose=False):
        self._client.SetClientCustomerId(account_id)
        ad_group_ad_service = self._client.GetService('AdGroupAdService', version=self._version)
        
        # construct operations
        operations = []
        for i, j in zip(df_data['Ad group ID'], df_data['Ad ID']):
            operations.append({'operator': 'REMOVE', 
                               'operand': {'xsi_type': 'AdGroupAd',
                                           'adGroupId': i,
                                           'ad': {'id': j}
                                          }
                               })
        # start deleting
        for i in xrange(0, len(operations), self._max_operations):
            tmp_operations = operations[i:i+self._max_operations]
            result = ad_group_ad_service.mutate(tmp_operations)
            if verbose:
                for ad in result['value']:
                    print ('Ad with id "{0}" and type "{1}" was deleted.'.format(ad['ad']['id'], ad['ad']['Ad.Type']))
    
    def run(self, countries, verbose=False):
        status = collections.OrderedDict()
        for country in countries:
            accounts = self.country_accounts(country)
            for _id in accounts:
                data = self.get_paused_stardard_text_ads(_id)
                status[accounts[_id]] = len(data)
                if len(data):
                    self.delete_multiple_ads(_id, data, verbose)
        return pd.DataFrame(status.items())

In [78]:
a = adwords_accounts('20171001', '20171020')

In [79]:
countries = a.get_all_countries()

In [80]:
value = a.run(list(countries), True)

Ad with id "104754243317" and type "TextAd" was deleted.
Ad with id "104752573397" and type "TextAd" was deleted.
Ad with id "90871057742" and type "TextAd" was deleted.
Ad with id "90871072262" and type "TextAd" was deleted.
Ad with id "90871055342" and type "TextAd" was deleted.
Ad with id "90871069142" and type "TextAd" was deleted.
Ad with id "90871062302" and type "TextAd" was deleted.
Ad with id "90871058942" and type "TextAd" was deleted.
Ad with id "90871060862" and type "TextAd" was deleted.
Ad with id "90871052942" and type "TextAd" was deleted.
Ad with id "90871057382" and type "TextAd" was deleted.
Ad with id "90871057502" and type "TextAd" was deleted.
Ad with id "90871070702" and type "TextAd" was deleted.
Ad with id "90871056902" and type "TextAd" was deleted.
Ad with id "90871071302" and type "TextAd" was deleted.
Ad with id "90871053302" and type "TextAd" was deleted.
Ad with id "90871060142" and type "TextAd" was deleted.
Ad with id "90871055822" and type "TextAd" was